In [57]:
from __future__ import absolute_import, division, print_function, unicode_literals
# import libraries
%matplotlib inline
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split

# TensorFlow and tf.keras
import tensorflow as tf
from tensorflow import keras

from tensorflow.keras.datasets import cifar10
from tensorflow.keras.models import Sequential 
from tensorflow.keras import layers
from tensorflow.keras import optimizers
# Helper libraries

print(tf.__version__)

2.4.1


In [99]:
#load and prepare data

path = os.getcwd() + '/final_data/vgsalesCleanedPublishers.csv'
data = pd.read_csv(path, header=0)

del data['Rank']
del data['Name']
#del data['Publisher']
del data['NA_Sales']
del data['EU_Sales']
del data['JP_Sales']
del data['Other_Sales']

target = data['Global_Sales']
del data['Global_Sales']

for t in range(len(target)):
    if target[t]> 10:
        target.at[t] = 9
    elif target[t]> 5:
       target.at[t]= 8
    elif target[t]>3:
       target.at[t]= 7
    elif target[t]>1:
       target.at[t]= 6
    elif target[t]>0.5:
       target.at[t]= 5
    elif target[t]>0.3:
       target.at[t]= 4
    elif target[t]>0.1:
       target.at[t]= 3
    elif target[t]>0.05:
       target.at[t]= 2
    elif target[t]>0.03:
       target.at[t]= 1
    elif target[t]>=0.01:
       target.at[t]= 0
print(target)

new_target = np.zeros((target.shape[0], 10))
for i in range(target.shape[0]):
    new_target[i, int(target.at[i])] = 1

platforms = {}
for p in data['Platform']:
    if p in platforms.keys():
        pass
    else:
        platforms[p] = len(platforms)
print(platforms)

genres = {}
for g in data['Genre']:
    if g in genres.keys():
        pass
    else:
        genres[g] = len(genres)
print(genres)

publishers = {}
for pu in data['Publisher']:
    if pu in publishers.keys():
        pass
    else:
        publishers[pu] = len(publishers)
print(publishers)

for i in range(data.shape[0]):
    data.at[i,'Platform'] = platforms[data['Platform'][i]]
    data.at[i, 'Genre'] = genres[data['Genre'][i]]
    data.at[i,'Publisher'] = publishers[data['Publisher'][i]]
print(data)


0        9.0
1        9.0
2        9.0
3        9.0
4        9.0
        ... 
16431    0.0
16432    0.0
16433    0.0
16434    0.0
16435    0.0
Name: Global_Sales, Length: 16436, dtype: float64
{'Wii': 0, 'NES': 1, 'GB': 2, 'DS': 3, 'X360': 4, 'PS3': 5, 'PS2': 6, 'SNES': 7, 'GBA': 8, '3DS': 9, 'PS4': 10, 'N64': 11, 'PS': 12, 'XB': 13, 'PC': 14, '2600': 15, 'PSP': 16, 'XOne': 17, 'GC': 18, 'WiiU': 19, 'GEN': 20, 'DC': 21, 'PSV': 22, 'SAT': 23, 'SCD': 24, 'WS': 25, 'NG': 26, 'TG16': 27, '3DO': 28, 'GG': 29, 'PCFX': 30}
{'Sports': 0, 'Platform': 1, 'Racing': 2, 'Role-Playing': 3, 'Puzzle': 4, 'Misc': 5, 'Shooter': 6, 'Simulation': 7, 'Action': 8, 'Fighting': 9, 'Adventure': 10, 'Strategy': 11}
{'Nintendo': 0, 'Microsoft Game Studios': 1, 'Take-Two Interactive': 2, 'Sony Computer Entertainment': 3, 'Activision': 4, 'Ubisoft': 5, 'Bethesda Softworks': 6, 'Electronic Arts': 7, 'Sega': 8, 'SquareSoft': 9, 'Atari': 10, '505 Games': 11, 'Capcom': 12, 'GT Interactive': 13, 'Konami Digital Enterta

      Platform  Year Genre Publisher
0            0  2006     0         0
1            1  1985     1         0
2            0  2008     2         0
3            0  2009     0         0
4            2  1996     3         0
...        ...   ...   ...       ...
16431        8  2002     1       187
16432       18  2003     6        51
16433        6  2008     2         4
16434        3  2010     4       507
16435        8  2003     1       170

[16436 rows x 4 columns]


In [100]:
#split and format data some more

x_train, x_test, y_train, y_test = train_test_split(data, new_target, test_size=2700, random_state=0)
x_train, x_valid, y_train, y_valid = train_test_split(x_train, y_train, test_size=2700, random_state=0)
print(x_train.shape)

x_train = np.asarray(x_train).astype(np.float32)
y_train = np.asarray(y_train).astype(np.float32)

x_test = np.asarray(x_test).astype(np.float32)
y_test = np.asarray(y_test).astype(np.float32)

x_valid = np.asarray(x_valid).astype(np.float32)
y_valid = np.asarray(y_valid).astype(np.float32)

(11036, 4)


In [144]:
# try to optimize parameters

first_activations = ['gelu', 'relu', 'selu', 'sigmoid']
losses = ['categorical_crossentropy', 'categorical_hinge', 'mean_absolute_error', 'poisson']
batch_sizes = [8, 16, 32, 64, 128]

accuracies = {}

for fa in first_activations:
    print(fa)
    accuracies[fa] = {}
    for los in losses:
        print(los)
        accuracies[fa][los] = {}
        for batch in batch_sizes:
            accuracies[fa][los][batch] = {}
            for drop in range(10, 21):
                accuracies[fa][los][batch][drop] = {}
                for dec in range(5, 11):
                    model = keras.Sequential()
                    model.add(keras.layers.Dense(150, activation=fa))
                    model.add(keras.layers.Dropout(float(drop/100)))
                    model.add(keras.layers.Dense(10, activation='softmax'))
                    model.compile(optimizer=keras.optimizers.SGD(learning_rate = .001, decay=float(dec/10000)), metrics=['accuracy'], loss=los)
    
                    model.fit(x_train, y_train, batch_size=batch, epochs=10, validation_data=(x_valid, y_valid))

                    accuracies[fa][los][batch][drop][dec] = model.evaluate(x_test, y_test, batch_size=batch)
    print('\n\n')
print(accuracies)


gelu
categorical_crossentropy
Epoch 1/10
1380/1380 [==============================] - 2s 1ms/step - loss: 28.0352 - accuracy: 0.2692 - val_loss: 2.2453 - val_accuracy: 0.2737
Epoch 2/10
1380/1380 [==============================] - 1s 977us/step - loss: 2.2356 - accuracy: 0.2789 - val_loss: 2.2140 - val_accuracy: 0.2737
Epoch 3/10
1380/1380 [==============================] - 1s 937us/step - loss: 2.2079 - accuracy: 0.2789 - val_loss: 2.1935 - val_accuracy: 0.2737
Epoch 4/10
1380/1380 [==============================] - 1s 948us/step - loss: 2.1893 - accuracy: 0.2749 - val_loss: 2.1787 - val_accuracy: 0.2737
Epoch 5/10
1380/1380 [==============================] - 1s 920us/step - loss: 2.1790 - accuracy: 0.2667 - val_loss: 2.1674 - val_accuracy: 0.2737
Epoch 6/10
1380/1380 [==============================] - 1s 949us/step - loss: 2.1664 - accuracy: 0.2706 - val_loss: 2.1584 - val_accuracy: 0.2737
Epoch 7/10
1380/1380 [==============================] - 1s 956us/step - loss: 2.1568 - accuracy

Epoch 4/10
1380/1380 [==============================] - 1s 950us/step - loss: 2.2142 - accuracy: 0.2783 - val_loss: 2.2078 - val_accuracy: 0.2737
Epoch 5/10
1380/1380 [==============================] - 1s 947us/step - loss: 2.2077 - accuracy: 0.2692 - val_loss: 2.2000 - val_accuracy: 0.2737
Epoch 6/10
1380/1380 [==============================] - 1s 950us/step - loss: 2.1970 - accuracy: 0.2805 - val_loss: 2.1938 - val_accuracy: 0.2737
Epoch 7/10
1380/1380 [==============================] - 1s 933us/step - loss: 2.1922 - accuracy: 0.2747 - val_loss: 2.1886 - val_accuracy: 0.2737
Epoch 8/10
1380/1380 [==============================] - 1s 931us/step - loss: 2.1901 - accuracy: 0.2691 - val_loss: 2.1842 - val_accuracy: 0.2737
Epoch 9/10
1380/1380 [==============================] - 1s 930us/step - loss: 2.1819 - accuracy: 0.2808 - val_loss: 2.1803 - val_accuracy: 0.2737
Epoch 10/10
338/338 [==============================] - 0s 674us/step - loss: 2.1755 - accuracy: 0.2830
Epoch 1/10
1380/1380 

Epoch 7/10
1380/1380 [==============================] - 1s 953us/step - loss: 2.1875 - accuracy: 0.2749 - val_loss: 2.1831 - val_accuracy: 0.2737
Epoch 8/10
1380/1380 [==============================] - 1s 957us/step - loss: 2.1825 - accuracy: 0.2746 - val_loss: 2.1784 - val_accuracy: 0.2737
Epoch 9/10
1380/1380 [==============================] - 1s 949us/step - loss: 2.1773 - accuracy: 0.2760 - val_loss: 2.1743 - val_accuracy: 0.2737
Epoch 10/10
338/338 [==============================] - 0s 641us/step - loss: 2.1692 - accuracy: 0.2830
Epoch 1/10
1380/1380 [==============================] - 2s 1ms/step - loss: 52.6606 - accuracy: 0.2806 - val_loss: 2.2542 - val_accuracy: 0.2737
Epoch 2/10
1380/1380 [==============================] - 1s 915us/step - loss: 2.2468 - accuracy: 0.2810 - val_loss: 2.2319 - val_accuracy: 0.2737
Epoch 3/10
1380/1380 [==============================] - 1s 922us/step - loss: 2.2279 - accuracy: 0.2757 - val_loss: 2.2179 - val_accuracy: 0.2737
Epoch 4/10
1380/1380 [

338/338 [==============================] - 0s 665us/step - loss: 2.1618 - accuracy: 0.2830
Epoch 1/10
1380/1380 [==============================] - 2s 1ms/step - loss: 29.9183 - accuracy: 0.2709 - val_loss: 2.2530 - val_accuracy: 0.2737
Epoch 2/10
1380/1380 [==============================] - 1s 962us/step - loss: 2.2457 - accuracy: 0.2786 - val_loss: 2.2293 - val_accuracy: 0.2737
Epoch 3/10
1380/1380 [==============================] - 1s 992us/step - loss: 2.2274 - accuracy: 0.2641 - val_loss: 2.2144 - val_accuracy: 0.2737
Epoch 4/10
1380/1380 [==============================] - 1s 971us/step - loss: 2.2128 - accuracy: 0.2723 - val_loss: 2.2036 - val_accuracy: 0.2737
Epoch 5/10
1380/1380 [==============================] - 1s 958us/step - loss: 2.2005 - accuracy: 0.2795 - val_loss: 2.1954 - val_accuracy: 0.2737
Epoch 6/10
1380/1380 [==============================] - 1s 948us/step - loss: 2.1937 - accuracy: 0.2743 - val_loss: 2.1887 - val_accuracy: 0.2737
Epoch 7/10
1380/1380 [============

1380/1380 [==============================] - 1s 936us/step - loss: 2.2449 - accuracy: 0.2677 - val_loss: 2.2260 - val_accuracy: 0.2737
Epoch 3/10
1380/1380 [==============================] - 1s 941us/step - loss: 2.2218 - accuracy: 0.2757 - val_loss: 2.2100 - val_accuracy: 0.2737
Epoch 4/10
1380/1380 [==============================] - 1s 918us/step - loss: 2.2062 - accuracy: 0.2764 - val_loss: 2.1984 - val_accuracy: 0.2737
Epoch 5/10
1380/1380 [==============================] - 1s 889us/step - loss: 2.1959 - accuracy: 0.2757 - val_loss: 2.1896 - val_accuracy: 0.2737
Epoch 6/10
1380/1380 [==============================] - 1s 905us/step - loss: 2.1884 - accuracy: 0.2733 - val_loss: 2.1825 - val_accuracy: 0.2737
Epoch 7/10
1380/1380 [==============================] - 1s 893us/step - loss: 2.1802 - accuracy: 0.2775 - val_loss: 2.1766 - val_accuracy: 0.2737
Epoch 8/10
1380/1380 [==============================] - 1s 929us/step - loss: 2.1756 - accuracy: 0.2746 - val_loss: 2.1715 - val_accura

...

87/87 [==============================] - 0s 1ms/step - loss: 0.3445 - accuracy: 0.1009 - val_loss: 0.3366 - val_accuracy: 0.1426
Epoch 9/10
87/87 [==============================] - 0s 1ms/step - loss: 0.3431 - accuracy: 0.1085 - val_loss: 0.3343 - val_accuracy: 0.1426
Epoch 10/10
22/22 [==============================] - 0s 512us/step - loss: 0.3314 - accuracy: 0.1415
Epoch 1/10
87/87 [==============================] - 1s 3ms/step - loss: 0.3515 - accuracy: 0.1336 - val_loss: 0.3398 - val_accuracy: 0.1056
Epoch 2/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3450 - accuracy: 0.1375 - val_loss: 0.3337 - val_accuracy: 0.1056
Epoch 3/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3377 - accuracy: 0.1596 - val_loss: 0.3286 - val_accuracy: 0.1056
Epoch 4/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3349 - accuracy: 0.1697 - val_loss: 0.3258 - val_accuracy: 0.1056
Epoch 5/10
87/87 [==============================] - 0s 2ms/step - loss

Epoch 3/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3588 - accuracy: 0.0942 - val_loss: 0.3506 - val_accuracy: 0.1419
Epoch 4/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3544 - accuracy: 0.1047 - val_loss: 0.3462 - val_accuracy: 0.1437
Epoch 5/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3504 - accuracy: 0.1070 - val_loss: 0.3425 - val_accuracy: 0.1437
Epoch 6/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3470 - accuracy: 0.1181 - val_loss: 0.3393 - val_accuracy: 0.1444
Epoch 7/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3422 - accuracy: 0.1328 - val_loss: 0.3366 - val_accuracy: 0.1456
Epoch 8/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3409 - accuracy: 0.1315 - val_loss: 0.3340 - val_accuracy: 0.1463
Epoch 9/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3379 - accuracy: 0.1414 - val_loss: 0.3319 - val_accuracy: 0.1470
Epoch 10/10
22/22 [=

87/87 [==============================] - 0s 1ms/step - loss: 0.3322 - accuracy: 0.1460 - val_loss: 0.3206 - val_accuracy: 0.1707
Epoch 9/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3288 - accuracy: 0.1541 - val_loss: 0.3189 - val_accuracy: 0.1715
Epoch 10/10
22/22 [==============================] - 0s 648us/step - loss: 0.3188 - accuracy: 0.1659
Epoch 1/10
87/87 [==============================] - 1s 3ms/step - loss: 0.3642 - accuracy: 0.0627 - val_loss: 0.3435 - val_accuracy: 0.0789
Epoch 2/10
87/87 [==============================] - 0s 1ms/step - loss: 0.3497 - accuracy: 0.0805 - val_loss: 0.3343 - val_accuracy: 0.0789
Epoch 3/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3427 - accuracy: 0.1028 - val_loss: 0.3292 - val_accuracy: 0.0789
Epoch 4/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3388 - accuracy: 0.1069 - val_loss: 0.3259 - val_accuracy: 0.0789
Epoch 5/10
87/87 [==============================] - 0s 2ms/step - loss

87/87 [==============================] - 0s 2ms/step - loss: 0.3591 - accuracy: 0.1066 - val_loss: 0.3474 - val_accuracy: 0.1244
Epoch 3/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3519 - accuracy: 0.1282 - val_loss: 0.3424 - val_accuracy: 0.2019
Epoch 4/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3473 - accuracy: 0.1553 - val_loss: 0.3355 - val_accuracy: 0.2433
Epoch 5/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3415 - accuracy: 0.1665 - val_loss: 0.3296 - val_accuracy: 0.2507
Epoch 6/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3378 - accuracy: 0.1733 - val_loss: 0.3275 - val_accuracy: 0.2544
Epoch 7/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3337 - accuracy: 0.1969 - val_loss: 0.3256 - val_accuracy: 0.2619
Epoch 8/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3331 - accuracy: 0.2037 - val_loss: 0.3241 - val_accuracy: 0.2637
Epoch 9/10
87/87 [=============

87/87 [==============================] - 0s 2ms/step - loss: 0.3215 - accuracy: 0.1933 - val_loss: 0.3124 - val_accuracy: 0.2874
Epoch 8/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3218 - accuracy: 0.2002 - val_loss: 0.3114 - val_accuracy: 0.2881
Epoch 9/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3208 - accuracy: 0.1989 - val_loss: 0.3105 - val_accuracy: 0.2852
Epoch 10/10
22/22 [==============================] - 0s 815us/step - loss: 0.3084 - accuracy: 0.2930
Epoch 1/10
87/87 [==============================] - 1s 5ms/step - loss: 0.4355 - accuracy: 0.0096 - val_loss: 0.3877 - val_accuracy: 0.0093
Epoch 2/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3946 - accuracy: 0.0205 - val_loss: 0.3726 - val_accuracy: 0.0093
Epoch 3/10
87/87 [==============================] - 0s 2ms/step - loss: 0.3824 - accuracy: 0.0390 - val_loss: 0.3620 - val_accuracy: 0.0093
Epoch 4/10
87/87 [==============================] - 0s 2ms/step - loss

In [148]:
#find best accuaracy

maxacc_mlp = 0
for fa in first_activations:
    for los in losses:
        for batch in batch_sizes:
            for drop in range(10, 21):
                for dec in range(5, 11):
                    if accuracies[fa][los][batch][drop][dec][1] > maxacc_mlp:
                        maxacc_mlp = accuracies[fa][los][batch][drop][dec][1]
                        print(fa, los, batch, drop, dec)
print(maxacc_mlp)

gelu categorical_crossentropy 8 10 5
gelu categorical_crossentropy 8 12 6
gelu categorical_crossentropy 64 10 8
gelu categorical_crossentropy 128 18 5
relu categorical_crossentropy 32 16 8
sigmoid categorical_hinge 8 19 5
0.30851852893829346


In [155]:
model = keras.Sequential()
model.add(keras.layers.Dense(150, activation='sigmoid'))
model.add(keras.layers.Dropout(.19))
model.add(keras.layers.Dense(10, activation='softmax'))
model.compile(optimizer=keras.optimizers.SGD(learning_rate = .001, decay=.0005), metrics=['accuracy'], loss='categorical_hinge')
    
model.fit(x_train, y_train, batch_size=8, epochs=10, validation_data=(x_valid, y_valid))
        
model.evaluate(x_test, y_test, batch_size=8)

Epoch 1/10
1380/1380 [==============================] - 2s 1ms/step - loss: 1.1374 - accuracy: 0.0714 - val_loss: 1.0063 - val_accuracy: 0.1481
Epoch 2/10
1380/1380 [==============================] - 1s 1ms/step - loss: 1.0725 - accuracy: 0.1456 - val_loss: 1.0211 - val_accuracy: 0.2978
Epoch 3/10
1380/1380 [==============================] - 1s 1ms/step - loss: 1.0700 - accuracy: 0.1693 - val_loss: 1.0205 - val_accuracy: 0.3015
Epoch 4/10
1380/1380 [==============================] - 1s 1ms/step - loss: 1.0690 - accuracy: 0.1695 - val_loss: 1.0217 - val_accuracy: 0.3007
Epoch 5/10
1380/1380 [==============================] - 1s 1ms/step - loss: 1.0698 - accuracy: 0.1697 - val_loss: 1.0225 - val_accuracy: 0.3007
Epoch 6/10
1380/1380 [==============================] - 2s 1ms/step - loss: 1.0669 - accuracy: 0.1787 - val_loss: 1.0233 - val_accuracy: 0.3015
Epoch 7/10
1380/1380 [==============================] - 1s 1ms/step - loss: 1.0686 - accuracy: 0.1771 - val_loss: 1.0230 - val_accuracy:

[1.0223463773727417, 0.30444443225860596]